In [1]:
from sqlalchemy import create_engine
from sqlalchemy.schema import Table, Column, ForeignKey, MetaData
from sqlalchemy.types import Integer, Text
from sqlalchemy.sql import insert, select, join, update

In [2]:
import numpy as np
import pandas as pd
import re
import math

In [3]:
meta = MetaData()

In [4]:
engine = create_engine('sqlite:///pillm.db', echo = True)

In [5]:
meta.bind = engine

In [6]:
Table('MY',meta,
     Column('PK',Integer, primary_key=True),
     Column('MY', Text, nullable=False)
     )

Table('MY', MetaData(bind=Engine(sqlite:///pillm.db)), Column('PK', Integer(), table=<MY>, primary_key=True, nullable=False), Column('MY', Text(), table=<MY>, nullable=False), schema=None)

In [7]:
Table('JH',meta,
     Column('PK',Integer, primary_key=True),
     Column('JH', Text, nullable=False)
     )

Table('JH', MetaData(bind=Engine(sqlite:///pillm.db)), Column('PK', Integer(), table=<JH>, primary_key=True, nullable=False), Column('JH', Text(), table=<JH>, nullable=False), schema=None)

In [8]:
Table('BH',meta,
     Column('PK',Integer, primary_key=True),
     Column('BH', Text, nullable=False)
     )

Table('BH', MetaData(bind=Engine(sqlite:///pillm.db)), Column('PK', Integer(), table=<BH>, primary_key=True, nullable=False), Column('BH', Text(), table=<BH>, nullable=False), schema=None)

In [9]:
Table('MED',meta,
    Column('PK',Integer, primary_key=True),
    Column('MY',Integer, ForeignKey('MY.PK')),
    Column('JH',Integer, ForeignKey('JH.PK')),
    Column('COLOR',Text, nullable=False),
    Column('BH_F',Integer, ForeignKey('BH.PK')),
    Column('BH_B',Integer, ForeignKey('BH.PK')),
    Column('TEXT_F',Text, nullable=True),
    Column('TEXT_B',Text, nullable=True)
    )

Table('MED', MetaData(bind=Engine(sqlite:///pillm.db)), Column('PK', Integer(), table=<MED>, primary_key=True, nullable=False), Column('MY', Integer(), ForeignKey('MY.PK'), table=<MED>), Column('JH', Integer(), ForeignKey('JH.PK'), table=<MED>), Column('COLOR', Text(), table=<MED>, nullable=False), Column('BH_F', Integer(), ForeignKey('BH.PK'), table=<MED>), Column('BH_B', Integer(), ForeignKey('BH.PK'), table=<MED>), Column('TEXT_F', Text(), table=<MED>), Column('TEXT_B', Text(), table=<MED>), schema=None)

In [10]:
meta.create_all()

2022-12-07 11:55:38,495 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2022-12-07 11:55:38,497 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("MY")
2022-12-07 11:55:38,497 INFO sqlalchemy.engine.Engine [raw sql] ()
2022-12-07 11:55:38,498 INFO sqlalchemy.engine.Engine PRAGMA temp.table_info("MY")
2022-12-07 11:55:38,499 INFO sqlalchemy.engine.Engine [raw sql] ()
2022-12-07 11:55:38,500 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("JH")
2022-12-07 11:55:38,501 INFO sqlalchemy.engine.Engine [raw sql] ()
2022-12-07 11:55:38,502 INFO sqlalchemy.engine.Engine PRAGMA temp.table_info("JH")
2022-12-07 11:55:38,502 INFO sqlalchemy.engine.Engine [raw sql] ()
2022-12-07 11:55:38,503 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("BH")
2022-12-07 11:55:38,503 INFO sqlalchemy.engine.Engine [raw sql] ()
2022-12-07 11:55:38,504 INFO sqlalchemy.engine.Engine PRAGMA temp.table_info("BH")
2022-12-07 11:55:38,505 INFO sqlalchemy.engine.Engine [raw sql] ()
2022-12-07 11:55:38,506 INFO 

In [11]:
meta.tables

FacadeDict({'MY': Table('MY', MetaData(bind=Engine(sqlite:///pillm.db)), Column('PK', Integer(), table=<MY>, primary_key=True, nullable=False), Column('MY', Text(), table=<MY>, nullable=False), schema=None), 'JH': Table('JH', MetaData(bind=Engine(sqlite:///pillm.db)), Column('PK', Integer(), table=<JH>, primary_key=True, nullable=False), Column('JH', Text(), table=<JH>, nullable=False), schema=None), 'BH': Table('BH', MetaData(bind=Engine(sqlite:///pillm.db)), Column('PK', Integer(), table=<BH>, primary_key=True, nullable=False), Column('BH', Text(), table=<BH>, nullable=False), schema=None), 'MED': Table('MED', MetaData(bind=Engine(sqlite:///pillm.db)), Column('PK', Integer(), table=<MED>, primary_key=True, nullable=False), Column('MY', Integer(), ForeignKey('MY.PK'), table=<MED>), Column('JH', Integer(), ForeignKey('JH.PK'), table=<MED>), Column('COLOR', Text(), table=<MED>, nullable=False), Column('BH_F', Integer(), ForeignKey('BH.PK'), table=<MED>), Column('BH_B', Integer(), Foreig

In [12]:
jh_dict = {3: '정제', 0: '경질캡슐', 2: '연질캡슐', 1: '기타'}
my_dict = {6: '원형',
              8: '장방형',
              9: '타원형',
              0: '기타',
              4: '삼각형',
              10: '팔각형',
              3: '사각형',
              5: '오각형',
              7: '육각형',
              1: '마름모형',
              2: '반원형'}
bh_dict = {2: 'x', 1: '-', 0: '+', 3: '기타'}

In [13]:
data = pd.read_csv('./merged_med_forDB.csv')

In [14]:
data.head()

ID         복사품목명                      품목명    표시앞  표시뒤  의약품제형 크기장축 크기단축  \
0   0   가스디알정50밀리그램  가스디알정50밀리그램(디메크로틴산마그네슘)    IDG    -      6  7.6  7.6   
1   1  페라트라정2.5밀리그램       페라트라정2.5밀리그램(레트로졸)     YH   LT      6  6.1  6.1   
2   2         졸뎀속붕정         졸뎀속붕정(졸피뎀타르타르산염)      -    -      6    9    9   
3   3         가스프렌정    가스프렌정(모사프리드시트르산염이수화물)     KD  분할선      8  9.1  4.5   
4   4          바르탄정               바르탄정(발사르탄)  V분할선T  HS8      6  6.5  6.5   

   제형코드명 표기내용앞 표기내용뒤 표기코드앞 표기코드뒤                                          url  \
0      3     -     -     -     -  http://medinavi.co.kr/pill/p/200808876.html   
1      3     -     -     -     -  http://medinavi.co.kr/pill/p/200808877.html   
2      3     -     -     -     -  http://medinavi.co.kr/pill/p/200808948.html   
3      3     -     -     -     -  http://medinavi.co.kr/pill/p/200809076.html   
4      3     -     -     -     -  http://medinavi.co.kr/pill/p/200809361.html   

   색상  앞분할선  뒤분할선  color  
0  연두     2     2  green  
1  노랑     2     2    red  
2  하양     2     2  white  
3  하양     2     1  white  
4  분홍     1     2    red

In [15]:
data.iloc[0]

ID                                                 0
복사품목명                                    가스디알정50밀리그램
품목명                          가스디알정50밀리그램(디메크로틴산마그네슘)
표시앞                                              IDG
표시뒤                                                -
의약품제형                                              6
크기장축                                             7.6
크기단축                                             7.6
제형코드명                                              3
표기내용앞                                              -
표기내용뒤                                              -
표기코드앞                                              -
표기코드뒤                                              -
url      http://medinavi.co.kr/pill/p/200808876.html
색상                                                연두
앞분할선                                               2
뒤분할선                                               2
color                                          green
Name: 0, dtype: object

In [16]:
data.replace('-',np.nan,inplace=True)

In [17]:
data.shape

(18776, 18)

In [18]:
med = meta.tables['MED']
my = meta.tables['MY']
jh = meta.tables['JH']
bh = meta.tables['BH']

In [20]:
for i in range(18776):
    engine.execute(med.insert().values(
        PK = int(data.iloc[i]['ID']),
        MY = int(data.iloc[i]['의약품제형']), 
        JH= int(data.iloc[i]['제형코드명']),
        BH_F= int(data.iloc[i]['앞분할선']),
        BH_B= int(data.iloc[i]['뒤분할선']),
        COLOR=data.iloc[i]['color'],
        TEXT_F=data.iloc[i]['표시앞'],
        TEXT_B=data.iloc[i]['표시뒤']
                                       ))

2022-12-07 11:56:55,273 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:56:55,274 INFO sqlalchemy.engine.Engine [generated in 0.00085s] (0, 6, 3, 'green', 2, 2, 'IDG', nan)
2022-12-07 11:56:55,279 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:56:55,287 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:56:55,288 INFO sqlalchemy.engine.Engine [cached since 0.01592s ago] (1, 6, 3, 'red', 2, 2, 'YH', 'LT')
2022-12-07 11:56:55,290 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:56:55,295 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:56:55,296 INFO sqlalchemy.engine.Engine [cached since 0.02391s ago] (2, 6, 3, 'white', 2, 2, nan, nan)
2022-12-07 11:56:55,297 I

2022-12-07 11:56:55,484 INFO sqlalchemy.engine.Engine [cached since 0.2112s ago] (23, 6, 3, 'red', 1, 2, '마크분할선C8', nan)
2022-12-07 11:56:55,486 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:56:55,494 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:56:55,495 INFO sqlalchemy.engine.Engine [cached since 0.2223s ago] (24, 6, 3, 'red', 1, 2, '마크분할선C16', nan)
2022-12-07 11:56:55,497 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:56:55,504 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:56:55,504 INFO sqlalchemy.engine.Engine [cached since 0.2317s ago] (25, 9, 3, 'red', 1, 2, 'R분할선Y', '160')
2022-12-07 11:56:55,506 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:56:55,512 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "

2022-12-07 11:56:55,715 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:56:55,716 INFO sqlalchemy.engine.Engine [cached since 0.4434s ago] (47, 6, 3, 'purple', 2, 2, 'INS', nan)
2022-12-07 11:56:55,718 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:56:55,725 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:56:55,725 INFO sqlalchemy.engine.Engine [cached since 0.4525s ago] (48, 8, 3, 'red', 2, 2, 'JIΛN', nan)
2022-12-07 11:56:55,727 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:56:55,733 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:56:55,734 INFO sqlalchemy.engine.Engine [cached since 0.4612s ago] (49, 8, 0, 'red', 2, 2, 'BTOORX', nan)
2022-12-07 11:56

2022-12-07 11:56:55,946 INFO sqlalchemy.engine.Engine [cached since 0.6737s ago] (70, 9, 2, 'green', 2, 2, 'DCD', nan)
2022-12-07 11:56:55,948 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:56:55,954 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:56:55,955 INFO sqlalchemy.engine.Engine [cached since 0.683s ago] (71, 8, 3, 'white', 2, 1, 'T32', '분할선')
2022-12-07 11:56:55,958 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:56:55,965 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:56:55,965 INFO sqlalchemy.engine.Engine [cached since 0.6931s ago] (72, 6, 3, 'red', 2, 2, 'T-32', nan)
2022-12-07 11:56:55,968 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:56:55,976 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F"

2022-12-07 11:56:56,223 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:56:56,224 INFO sqlalchemy.engine.Engine [cached since 0.9516s ago] (94, 8, 1, 'white', 2, 2, '552', nan)
2022-12-07 11:56:56,226 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:56:56,233 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:56:56,234 INFO sqlalchemy.engine.Engine [cached since 0.9615s ago] (95, 8, 0, 'red', 2, 2, 'BTOCN', nan)
2022-12-07 11:56:56,236 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:56:56,243 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:56:56,244 INFO sqlalchemy.engine.Engine [cached since 0.9719s ago] (96, 8, 0, 'blue', 2, 2, '이젠이이젠이', nan)
2022-12-07 11:5

...

2022-12-07 11:59:38,768 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:38,773 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:59:38,774 INFO sqlalchemy.engine.Engine [cached since 163.5s ago] (18666, 6, 3, 'red', 2, 2, 'KDC', '14')
2022-12-07 11:59:38,775 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:38,780 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:59:38,781 INFO sqlalchemy.engine.Engine [cached since 163.5s ago] (18667, 9, 3, 'red', 2, 2, 'NGP40', nan)
2022-12-07 11:59:38,782 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:38,788 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:59:38,789 INFO sqlalchemy.engine.Engine [cached since 163.

2022-12-07 11:59:38,963 INFO sqlalchemy.engine.Engine [cached since 163.7s ago] (18689, 6, 3, 'red', 2, 2, 'JWS', '10')
2022-12-07 11:59:38,965 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:38,970 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:59:38,971 INFO sqlalchemy.engine.Engine [cached since 163.7s ago] (18690, 6, 3, 'red', 2, 2, '10', 'INO')
2022-12-07 11:59:38,972 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:38,978 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:59:38,979 INFO sqlalchemy.engine.Engine [cached since 163.7s ago] (18691, 9, 3, 'white', 2, 0, '마크MP', '십자분할선')
2022-12-07 11:59:38,982 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:38,989 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B",

2022-12-07 11:59:39,165 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:39,171 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:59:39,171 INFO sqlalchemy.engine.Engine [cached since 163.9s ago] (18713, 6, 3, 'white', 2, 2, 'W-5', nan)
2022-12-07 11:59:39,173 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:39,178 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:59:39,179 INFO sqlalchemy.engine.Engine [cached since 163.9s ago] (18714, 6, 3, 'red', 1, 2, 'MUL분할선', 'HMP')
2022-12-07 11:59:39,181 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:39,188 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:59:39,188 INFO sqlalchemy.engine.Engine [cached since 

2022-12-07 11:59:39,377 INFO sqlalchemy.engine.Engine [cached since 164.1s ago] (18736, 6, 3, 'white', 2, 2, 'BS3', 'INO')
2022-12-07 11:59:39,379 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:39,385 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:59:39,386 INFO sqlalchemy.engine.Engine [cached since 164.1s ago] (18737, 8, 3, 'red', 2, 2, 'U/S', 'INO')
2022-12-07 11:59:39,388 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:39,395 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:59:39,396 INFO sqlalchemy.engine.Engine [cached since 164.1s ago] (18738, 8, 0, 'white', 2, 2, 'CLP243', nan)
2022-12-07 11:59:39,397 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:39,403 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B

2022-12-07 11:59:39,591 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:39,596 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:59:39,597 INFO sqlalchemy.engine.Engine [cached since 164.3s ago] (18760, 8, 3, 'red', 2, 2, 'HLMBD500', nan)
2022-12-07 11:59:39,599 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:39,606 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:59:39,607 INFO sqlalchemy.engine.Engine [cached since 164.3s ago] (18761, 6, 3, 'red', 2, 2, 'NZ', nan)
2022-12-07 11:59:39,609 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 11:59:39,615 INFO sqlalchemy.engine.Engine INSERT INTO "MED" ("PK", "MY", "JH", "COLOR", "BH_F", "BH_B", "TEXT_F", "TEXT_B") VALUES (?, ?, ?, ?, ?, ?, ?, ?)
2022-12-07 11:59:39,616 INFO sqlalchemy.engine.Engine [cached since 164

In [21]:
jh_dict,my_dict,bh_dict

({3: '정제', 0: '경질캡슐', 2: '연질캡슐', 1: '기타'},
 {6: '원형',
  8: '장방형',
  9: '타원형',
  0: '기타',
  4: '삼각형',
  10: '팔각형',
  3: '사각형',
  5: '오각형',
  7: '육각형',
  1: '마름모형',
  2: '반원형'},
 {2: 'x', 1: '-', 0: '+', 3: '기타'})

In [23]:
for k,v in jh_dict.items():
    print(k,v)

3 정제
0 경질캡슐
2 연질캡슐
1 기타


In [24]:
for k,v in jh_dict.items():
    engine.execute(jh.insert().values(
        PK=int(k),
        JH=v
    ))

2022-12-07 12:00:14,766 INFO sqlalchemy.engine.Engine INSERT INTO "JH" ("PK", "JH") VALUES (?, ?)
2022-12-07 12:00:14,771 INFO sqlalchemy.engine.Engine [generated in 0.00071s] (3, '정제')
2022-12-07 12:00:14,783 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 12:00:14,789 INFO sqlalchemy.engine.Engine INSERT INTO "JH" ("PK", "JH") VALUES (?, ?)
2022-12-07 12:00:14,790 INFO sqlalchemy.engine.Engine [cached since 0.01934s ago] (0, '경질캡슐')
2022-12-07 12:00:14,792 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 12:00:14,797 INFO sqlalchemy.engine.Engine INSERT INTO "JH" ("PK", "JH") VALUES (?, ?)
2022-12-07 12:00:14,797 INFO sqlalchemy.engine.Engine [cached since 0.02674s ago] (2, '연질캡슐')
2022-12-07 12:00:14,799 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 12:00:14,804 INFO sqlalchemy.engine.Engine INSERT INTO "JH" ("PK", "JH") VALUES (?, ?)
2022-12-07 12:00:14,805 INFO sqlalchemy.engine.Engine [cached since 0.03417s ago] (1, '기타')
2022-12-07 12:00:14,806 INFO sqlalchemy.engine.Engine COM

In [25]:
for k,v in bh_dict.items():
    engine.execute(bh.insert().values(
        PK=int(k),
        BH=v
    ))

2022-12-07 12:00:16,963 INFO sqlalchemy.engine.Engine INSERT INTO "BH" ("PK", "BH") VALUES (?, ?)
2022-12-07 12:00:16,965 INFO sqlalchemy.engine.Engine [generated in 0.00102s] (2, 'x')
2022-12-07 12:00:16,976 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 12:00:16,982 INFO sqlalchemy.engine.Engine INSERT INTO "BH" ("PK", "BH") VALUES (?, ?)
2022-12-07 12:00:16,982 INFO sqlalchemy.engine.Engine [cached since 0.01879s ago] (1, '-')
2022-12-07 12:00:16,984 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 12:00:16,989 INFO sqlalchemy.engine.Engine INSERT INTO "BH" ("PK", "BH") VALUES (?, ?)
2022-12-07 12:00:16,991 INFO sqlalchemy.engine.Engine [cached since 0.02698s ago] (0, '+')
2022-12-07 12:00:16,992 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 12:00:16,996 INFO sqlalchemy.engine.Engine INSERT INTO "BH" ("PK", "BH") VALUES (?, ?)
2022-12-07 12:00:16,997 INFO sqlalchemy.engine.Engine [cached since 0.03299s ago] (3, '기타')
2022-12-07 12:00:16,998 INFO sqlalchemy.engine.Engine COMMIT


In [26]:
for k,v in my_dict.items():
    engine.execute(my.insert().values(
        PK=int(k),
        MY=v
    ))

2022-12-07 12:00:17,550 INFO sqlalchemy.engine.Engine INSERT INTO "MY" ("PK", "MY") VALUES (?, ?)
2022-12-07 12:00:17,551 INFO sqlalchemy.engine.Engine [generated in 0.00101s] (6, '원형')
2022-12-07 12:00:17,560 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 12:00:17,565 INFO sqlalchemy.engine.Engine INSERT INTO "MY" ("PK", "MY") VALUES (?, ?)
2022-12-07 12:00:17,566 INFO sqlalchemy.engine.Engine [cached since 0.01712s ago] (8, '장방형')
2022-12-07 12:00:17,568 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 12:00:17,573 INFO sqlalchemy.engine.Engine INSERT INTO "MY" ("PK", "MY") VALUES (?, ?)
2022-12-07 12:00:17,574 INFO sqlalchemy.engine.Engine [cached since 0.02446s ago] (9, '타원형')
2022-12-07 12:00:17,575 INFO sqlalchemy.engine.Engine COMMIT
2022-12-07 12:00:17,580 INFO sqlalchemy.engine.Engine INSERT INTO "MY" ("PK", "MY") VALUES (?, ?)
2022-12-07 12:00:17,580 INFO sqlalchemy.engine.Engine [cached since 0.03117s ago] (0, '기타')
2022-12-07 12:00:17,582 INFO sqlalchemy.engine.Engine COMMI

In [ ]:
engine.execute(select([]))